In [ ]:
from pandas import DataFrame
import matplotlib.pyplot as plt
from DATA225utils import make_connection, dataframe_query

%matplotlib inline

In [ ]:
conn = make_connection(config_file='stock-prices.ini')

In [ ]:
def compute_exponential_smoothing(conn, alpha, label):
    """
    @cursor the database cursor
    @alpha the alpha value for exponential smoothing
    @label label for the exponentially smoothed values
    """
    conn.cursor().execute('SET @smoothed = NULL')
    
    _, df = dataframe_query(conn,
            f'SELECT days_ago, price, '
            f'       @smoothed := ({alpha}*price '
            f'                  + (1-{alpha})*(IF (@smoothed IS NULL, price, @smoothed))) '
            f'           AS {label} '
            f'FROM recent_prices '
            f'ORDER BY days_ago'
    )
    
    return df

In [ ]:
plt.figure(figsize=(15, 10))

first = True

for smoother in [5, 2]:
    graph_label = f'zero_point_{smoother}_exponentially_smoothed'
    alpha = smoother/10
    
    df = compute_exponential_smoothing(conn, alpha, graph_label)
    display(df)

    rows = df.values.tolist()
    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    exps = [row[2] for row in rows]
    
    # Initialize the graph.
    if first:
        plt.xticks(xs)
        plt.plot(xs, ys, linewidth=5)
        plt.title('Exponentially Smoothed Stock Prices')
        plt.xlabel('Days ago')
        plt.ylabel('Price')
        first = False

    # Plot the moving average line.
    plt.plot(xs, exps, label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
plt.figure(figsize=(15, 10))

first = True

for smoother in [5, 2]:
    graph_label = f'zero_point_{smoother}_exponentially_smoothed'
    alpha = smoother/10
    
    df = compute_exponential_smoothing(conn, alpha, graph_label)
    display(df)

    rows = df.values.tolist()
    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    exps = [row[2] for row in rows]
    
    # Initialize the graph.
    if first:
        plt.xticks(xs)
        plt.plot(xs, ys, linewidth=5)
        plt.title('Exponentially Smoothed Stock Prices')
        plt.xlabel('Days ago')
        plt.ylabel('Price')
        first = False

    # Plot the moving average line.
    plt.plot(xs, exps, label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
conn.close()

#### (c) 2023 by Ronald Mak